## Make a program to choose randomly p fraction of the population to infect initially
* Randomly with choosen probability picks 0 and 1 
* We find list of all unique users and then we need to infect a percentage of population
* Again a problem here is that we need to start infecting users only after a particular time
* we need to make this set to be positive or negative

**I propose that there could be atleast two mechanism to start infection**
1. Randomly infect people by choosing them after a particular time
2. Randomly infect people by choosing a particular place at particular time (this is how COVID started)
3. If choosing step 2 then we can randmly infect people who were at that place at a particular time
4. Using alpha as infection rate

In [1]:
import pandas as pd

df = pd.read_csv("processedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

Import the ArcGIS API for Python. This adds a GeoAccessor and spatially enables your DataFrame objects. As you will see in this notebook, you can then easily plot your data both as charts and as maps.

In [2]:
import matplotlib.pyplot as plt
%matplotlib inline

from arcgis.gis import GIS
from arcgis.features import GeoAccessor, GeoSeriesAccessor

/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/_data/geodataset/utils.py:15: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  pd.datetime,


# EXTRA IDEAS
## We can use venue catorgories to define the probabilty of infection
* If it is a closed space we can have more probability 
* If it is public space which is frequented by many we can give more probability
* Also we can give probability of contamination by looking at how many people were there at the place at given time

In [3]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We set the randomly chosen population to be infected

In [4]:
import numpy as np

alpha = 0.1

#choosing unique users from list of all user IDs
unique_users =  pd.unique(df["User ID (anonymized)"])#.

print(f"Number of unique users are: {len(unique_users)}")

# this is when we are infecting people after a particular time
gen_positive = np.random.choice((1,0),size = len(unique_users), p=[alpha, 1-alpha])

#Choosing the time at which infection begins
infect_time = df.iloc[2000]["Time"]

infections = np.sum(gen_positive)
print(f"Number of infected users: {infections}")

Number of unique users are: 1083
Number of infected users: 105


In [5]:
#Query logic to select only those users whose user id and time matches or  those who are positive already
for i in range(len(unique_users)):
    #print(i)
    if gen_positive[i] == 1:
        #Below query gives sets status to 1 if infected userId and time condition matches
        df["Status"]= np.where( ( (df["User ID (anonymized)"] == unique_users[i]) & (df["Time"] >= infect_time) ) | (df["Status"] == 1),1,0)

# Setting infection time for all
df["InfectionTime"] = np.where(df["Status"]==1,infect_time,0)

count_infected = len(df[df["Status"]==1])
print(f"number of infect rows: {count_infected}")

number of infect rows: 21285


In [6]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We need to do following
* We need to find every person that has been infected
* for every person that has been infected we need to find the other person who was at same place and time range
* infect these people with certain probability


    print(f"Meeting population for \n{infector}")
    print(meeting_population, i)
    for j in range(0,len(meeting_population)):
        person = df.iloc[meeting_population[j]]
        if(person["Status"]==0):
            print("Non infected person met.................")
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
                #Find all the entries of this person after this time and set details
                person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                print("Places where this person has rows")
                print(person_rows)
                for k in range(len(person_rows)):
                    df.iloc[meeting_population[j]]["Status"] = 1
                    df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                    df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
        else:
            # It might so happen that 1st infector was not processed to infect first
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
          
                if(person["InfectionTime"] >= person["Time"]):
                    print("Infected already........")
                else:
                    #Find all the entries of this person after this time and set details
                    print("Updating new infector.....................")
                    person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                    print("Places where this person has rows")
                    print(person_rows)
                    for k in range(len(person_rows)):
                        df.iloc[meeting_population[j]]["Status"] = 1
                        df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                        df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
    

In [7]:
# Find all the infected rows
infected_users_dataframe = df[df["Status"]==1]
print("List of infected users")
infected_users_dataframe

List of infected users


User ID (anonymized)     Venue ID (Foursquare)  \
2004                     979  4c006f47efa2ef3bf74baa8c   
2009                     826  4b4cca8bf964a52010bf26e3   
2011                     400  40b68100f964a5207d001fe3   
2012                     979  4e2c85ccd164223a698d6b22   
2027                     826  4b4bc134f964a52093a626e3   
...                      ...                       ...   
227389                   498  4c781867bd346dcbbbf6f0ef   
227397                   542  4be1db7dedbb0f47c5eaa615   
227407                   700  4a0798f6f964a52088731fe3   
227416                   751  41005500f964a5204e0b1fe3   
227421                   313  42e82000f964a52085261fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
2004         4bf58dd8d48988d1e2941735                           Beach   
2009         4bf58dd8d48988d1dd931735                      Soup Place   
2011         4bf58dd8d48988d163941735                            Park   
2012         4bf58dd8d48988d1e2941735                           Beach   
2027         4bf58dd8d48988d1e0931735                     Coffee Shop   
...                               ...                             ...   
227389       4bf58dd8d48988d1f9931735                            Road   
227397       4bf58dd8d48988d1a3941735       College Academic Building   
227407       4bf58dd8d48988d155941735                       Gastropub   
227416       4bf58dd8d48988d116941735                             Bar   
227421       4bf58dd8d48988d1db931735                Tapas Restaurant   

         Latitude  Longitude  Timezone offset(minutes)  \
2004    40.573935 -74.084287                      -240   
2009    40.760165 -73.983080                      -240   
2011    40.742188 -73.987924                      -240   
2012    40.590579 -74.066205                      -240   
2027    40.760802 -73.983493                      -240   
...           ...        ...                       ...   
227389  40.628895 -74.005760                      -300   
227397  40.776677 -73.980567                      -300   
227407  40.754070 -73.992263                      -300   
227416  40.666674 -73.988171                      -300   
227421  40.679334 -73.968326                      -300   

                              UTC time  Status  Iteration  InfectorId  \
2004    Wed Apr 04 17:21:27 +0000 2012       1          0           0   
2009    Wed Apr 04 17:23:27 +0000 2012       1          0           0   
2011    Wed Apr 04 17:24:03 +0000 2012       1          0           0   
2012    Wed Apr 04 17:24:08 +0000 2012       1          0           0   
2027    Wed Apr 04 17:30:14 +0000 2012       1          0           0   
...                                ...     ...        ...         ...   
227389  Sat Feb 16 01:51:40 +0000 2013       1          0           0   
227397  Sat Feb 16 02:02:48 +0000 2013       1          0           0   
227407  Sat Feb 16 02:12:44 +0000 2013       1          0           0   
227416  Sat Feb 16 02:19:07 +0000 2013       1          0           0   
227421  Sat Feb 16 02:27:49 +0000 2013       1          0           0   

        InfectionTime        Time  
2004       1333559854  1333560087  
2009       1333559854  1333560207  
2011       1333559854  1333560243  
2012       1333559854  1333560248  
2027       1333559854  1333560614  
...               ...         ...  
227389     1333559854  1360979500  
227397     1333559854  1360980168  
227407     1333559854  1360980764  
227416     1333559854  1360981147  
227421     1333559854  1360981669  

[21285 rows x 13 columns]

In [8]:
# Find all the infected users
infected_users_dataframe = df[df["Status"]==1]
infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
print("Infected Users are: ")
print(infected_users)
#count number of infections
infections = len(infected_users)
print(f"Total infections are: {infections}")
# Infection list stores list of infected people per round of simulation
infection_list = []
infection_list.append(infected_users)
# We need to find all the users who where at the same place as the infected user and in time range of 1 hrs
# 1hr = 3600 seconds
# ITERATING OVER ALL ROWS AND CHECKING TIME
iteration_count = 0
while(infections!=0):
    # we will maintain this variable to fetch inly new infections
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")
    infected_rows = len(infected_users_dataframe)
    for i in range(infected_rows):
        print(f"Calculating for infected person: {i} of {infected_rows}")
        infector = infected_users_dataframe.iloc[i]
        
        ##print("Infector is:")
        ##print("###################################################################")
        ##print(infector)
        ##print("###################################################################")
        
        # Finding all those prople infector meets after start of infection time
        # meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"])  & (df["Time"] >= infect_time))[0])
        
        # Finding all people that infector meets at infectors time range
        # Meeting Population is the list of indices of the people, not the User Id (anonymized)
        # We are keeping 3 hours time window -1 +2
        
        meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"]) & ( (df["Time"] >= (infector["Time"]-3600)) & (df["Time"] <= (infector["Time"]+7200)) ))[0])
        
        print("List of people this infector meets: "+str({len(meeting_population)})) 
        ##print(meeting_population)
        ##print(meeting_population)
        
        for index in meeting_population:
            person = df.iloc[index]
            if(person["Status"]==0):
                
                print(f"Non infected person met.................{index}")
                ##print("In range.............................")
                #Find all the entries of this person after this time and set details
                
                person_rows = np.where( (df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0]
                
                ##print("Places where this person has rows")
                ##print(f"Rows of person is : {len(person_rows)}")
                
                # TO MAKE MORE EFFIECIENT
                # https://stackoverflow.com/questions/49447233/python-maintain-multiple-columns-with-np-where
                for k in range(len(person_rows)):
                    df.at[index, "Status"] = 1
                    #print("Status Set")
                    df.at[index, "InfectorId"] = infector["User ID (anonymized)"]
                    #print("Infector Id Set")
                    df.at[index, "InfectionTime"] = person["Time"]
                    #print("Infection Time Set")
                    df.at[index, "Iteration"] = iteration_count+1
                    df.at[index, "InfectionLongitude"] = infector["Longitude"]
                    df.at[index, "InfectionLatitude"] = infector["Latitude"]
            else:
                # AS data is sorted with time we assume that we don't need tp bother who infects first
                print(f"Met with an already infected person.................{index}")
                
    # Find all the infected users
    # HERE WE MUST ALSO SET CONDITIONS BASED ON ITERATION, FETCH ONLY THAT WERE INFECTED IN THIS ITERATION
    iteration_count += 1
    print("Finding new Infections............................")
    infected_users_dataframe = df[(df["Status"]==1) & (df["Iteration"]==iteration_count)]
    infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
    infection_list.append(infected_users)
    ##print("Infected Users are: ")
    ##print(infected_users)
    #count number of infections
    print("Infected Users are: ")
    print(infected_users)
    infections = len(infected_users)
    print(f"Total new infections are: {infections}") 
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")

Infected Users are: 
[ 979  826  400  565  806  178  311  274  120  751  505  317 1057  572
  195 1005 1014  742  830   73 1060  529   12  564 1019  144  414  936
  265  405   15  891  473  339 1064  593 1074  250  847  162  957  362
  337  478  313  105  228  763  161   57  625  365   85  380  214  255
  251  413 1058   44  399  952 1028  423  334  698 1015    2  861  361
  295   59 1072  726  150  384  904  863  453  498  504  393  421  351
  385   27  813   98  103  416  954  921  550  815  382  729   77   41
    5  263  580  700   68  542  687]
Total infections are: 105
#############################################################################
#############################################################################
#############################################################################
Calculating for infected person: 0 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2004
Calculating for infected person: 1 of 21285


List of people this infector meets: {1}
Met with an already infected person.................2627
Calculating for infected person: 72 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2630
Calculating for infected person: 73 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2633
Calculating for infected person: 74 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2676
Calculating for infected person: 75 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2677
Calculating for infected person: 76 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2678
Calculating for infected person: 77 of 21285
List of people this infector meets: {1}
Met with an already infected person.................2680
Calculating for infected person: 78 of 21285
List o

List of people this infector meets: {2}
Non infected person met.................3457
Met with an already infected person.................3459
Calculating for infected person: 137 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3465
Calculating for infected person: 138 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3482
Calculating for infected person: 139 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3484
Calculating for infected person: 140 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3499
Calculating for infected person: 141 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3502
Calculating for infected person: 142 of 21285
List of people this infector meets: {1}
Met with an already infected person.................3504


Met with an already infected person.................4289
Non infected person met.................4381
Calculating for infected person: 217 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4290
Calculating for infected person: 218 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4296
Calculating for infected person: 219 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4338
Calculating for infected person: 220 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4342
Calculating for infected person: 221 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4346
Calculating for infected person: 222 of 21285
List of people this infector meets: {1}
Met with an already infected person.................4363
Calculating for infected person: 223 of 

Non infected person met.................5250
Met with an already infected person.................5267
Non infected person met.................5286
Non infected person met.................5314
Non infected person met.................5315
Met with an already infected person.................5323
Non infected person met.................5324
Non infected person met.................5338
Non infected person met.................5348
Met with an already infected person.................5354
Non infected person met.................5366
Non infected person met.................5375
Non infected person met.................5377
Non infected person met.................5384
Non infected person met.................5385
Non infected person met.................5400
Non infected person met.................5403
Non infected person met.................5418
Non infected person met.................5434
Calculating for infected person: 291 of 21285
List of people this infector meets: {1}
Met with an already inf

...

Calculating for infected person: 3 of 48
List of people this infector meets: {8}
Met with an already infected person.................31083
Met with an already infected person.................31089
Met with an already infected person.................31096
Met with an already infected person.................31103
Non infected person met.................31160
Non infected person met.................31177
Non infected person met.................31178
Non infected person met.................31201
Calculating for infected person: 4 of 48
List of people this infector meets: {8}
Met with an already infected person.................31083
Met with an already infected person.................31089
Met with an already infected person.................31096
Met with an already infected person.................31103
Met with an already infected person.................31160
Met with an already infected person.................31177
Met with an already infected person.................31178
Met with an alre

List of people this infector meets: {4}
Met with an already infected person.................169539
Non infected person met.................169544
Non infected person met.................169546
Non infected person met.................169547
Calculating for infected person: 34 of 48
List of people this infector meets: {5}
Met with an already infected person.................169612
Met with an already infected person.................169615
Met with an already infected person.................169634
Met with an already infected person.................169641
Met with an already infected person.................169667
Calculating for infected person: 35 of 48
List of people this infector meets: {6}
Met with an already infected person.................172932
Met with an already infected person.................172949
Met with an already infected person.................172972
Met with an already infected person.................173003
Met with an already infected person.................173038
Non in

Non infected person met.................31703
Non infected person met.................31706
Non infected person met.................31707
Calculating for infected person: 8 of 23
List of people this infector meets: {2}
Met with an already infected person.................49663
Non infected person met.................49872
Calculating for infected person: 9 of 23
List of people this infector meets: {4}
Met with an already infected person.................121815
Met with an already infected person.................121825
Non infected person met.................121841
Non infected person met.................121847
Calculating for infected person: 10 of 23
List of people this infector meets: {4}
Met with an already infected person.................121815
Met with an already infected person.................121825
Met with an already infected person.................121841
Met with an already infected person.................121847
Calculating for infected person: 11 of 23
List of people this infe

Calculating for infected person: 14 of 21
List of people this infector meets: {9}
Met with an already infected person.................181449
Met with an already infected person.................181459
Met with an already infected person.................181466
Met with an already infected person.................181470
Met with an already infected person.................181471
Met with an already infected person.................181474
Met with an already infected person.................181479
Met with an already infected person.................181493
Met with an already infected person.................181499
Calculating for infected person: 15 of 21
List of people this infector meets: {8}
Met with an already infected person.................181459
Met with an already infected person.................181466
Met with an already infected person.................181470
Met with an already infected person.................181471
Met with an already infected person.................181474
Met with a

List of people this infector meets: {5}
Met with an already infected person.................181559
Met with an already infected person.................181575
Met with an already infected person.................181581
Met with an already infected person.................181583
Met with an already infected person.................181584
Calculating for infected person: 3 of 5
List of people this infector meets: {6}
Met with an already infected person.................181559
Met with an already infected person.................181575
Met with an already infected person.................181581
Met with an already infected person.................181583
Met with an already infected person.................181584
Met with an already infected person.................181611
Calculating for infected person: 4 of 5
List of people this infector meets: {6}
Met with an already infected person.................181559
Met with an already infected person.................181575
Met with an already infected pers

In [9]:
#Check number of infection rounds
len(infection_list)

11

In [10]:
# Check number of infections per round
y = [len(x) for x in infection_list]
y


[105, 589, 187, 68, 43, 20, 19, 6, 2, 4, 0]

In [11]:
# Total infected individuals 
sum(y)

1043

In [12]:
# Write infected dataframe to the file
df.to_csv("NYCInfectedTMSC2014.tsv", sep="\t")

# Visualization
Geographic visualization of new infections at each iteration. Discrete and heat maps are displayed.

In [13]:
df = pd.read_csv("NYCInfectedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

gis = GIS()

In [14]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  InfectionLongitude  InfectionLatitude  
0                   0  1333476009                 NaN                NaN  
1                   0  1333476025                 NaN                NaN  
2                   0  1333476144                 NaN                NaN  
3                   0  1333476161                 NaN                NaN  
4                   0  1333476180                 NaN                NaN  
...               ...         ...                 ...                ...  
227423              0  1360981751                 NaN                NaN  
227424              0  1360981895                 NaN                NaN  
227425              0  1360981996                 NaN                NaN  
227426              0  1360982071                 NaN                NaN  
227427              0  1360982136  

In [15]:
print(infection_list[0])

[ 979  826  400  565  806  178  311  274  120  751  505  317 1057  572
  195 1005 1014  742  830   73 1060  529   12  564 1019  144  414  936
  265  405   15  891  473  339 1064  593 1074  250  847  162  957  362
  337  478  313  105  228  763  161   57  625  365   85  380  214  255
  251  413 1058   44  399  952 1028  423  334  698 1015    2  861  361
  295   59 1072  726  150  384  904  863  453  498  504  393  421  351
  385   27  813   98  103  416  954  921  550  815  382  729   77   41
    5  263  580  700   68  542  687]


In [16]:
df.shape

(227428, 15)

In [17]:
df.columns

Index(['User ID (anonymized)', 'Venue ID (Foursquare)',
       'Venue category ID (Foursquare)', 'Venue category name (Fousquare)',
       'Latitude', 'Longitude', 'Timezone offset(minutes)', 'UTC time',
       'Status', 'Iteration', 'InfectorId', 'InfectionTime', 'Time',
       'InfectionLongitude', 'InfectionLatitude'],
      dtype='object')

In [18]:
infected_df = df[df["User ID (anonymized)"].isin(infection_list[1]) 
                  & (df["Status"]==1) 
                  & (df["Iteration"]==1)]

In [19]:
infected_df

User ID (anonymized)     Venue ID (Foursquare)  \
2013                     601  40b68100f964a5207d001fe3   
2160                     881  4c524854384c76b00080f62a   
2962                     527  4ad8add6f964a520a61321e3   
3457                      14  49c27575f964a520f1551fe3   
3529                     121  4e4fe3902271a1bdc3e47f05   
...                      ...                       ...   
225605                   834  4840fe6bf964a52030501fe3   
225890                   719  42911d00f964a520f5231fe3   
226357                    82  50fdfffce4b011743dc5be9c   
227145                   801  4acc9126f964a520fcc820e3   
227282                   893  43a52546f964a520532c1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
2013         4bf58dd8d48988d163941735                            Park   
2160         4bf58dd8d48988d103941735                  Home (private)   
2962         4bf58dd8d48988d1fd931735                          Subway   
3457         4bf58dd8d48988d1fa941735               Food & Drink Shop   
3529         4bf58dd8d48988d103941735                  Home (private)   
...                               ...                             ...   
225605       4bf58dd8d48988d1fe931735                     Bus Station   
225890       4bf58dd8d48988d129951735                   Train Station   
226357       4bf58dd8d48988d103941735                  Home (private)   
227145       4bf58dd8d48988d132941735                          Church   
227282       4bf58dd8d48988d1ed931735                         Airport   

         Latitude  Longitude  Timezone offset(minutes)  \
2013    40.742188 -73.987924                      -240   
2160    40.833165 -73.941860                      -240   
2962    40.735734 -73.990568                      -240   
3457    40.736527 -73.990560                      -240   
3529    40.602590 -73.988880                      -240   
...           ...        ...                       ...   
225605  40.757221 -73.991547                      -300   
225890  40.750795 -73.993576                      -300   
226357  40.725541 -73.741902                      -300   
227145  40.769619 -73.984705                      -300   
227282  40.645089 -73.784523                      -300   

                              UTC time  Status  Iteration  InfectorId  \
2013    Wed Apr 04 17:25:03 +0000 2012       1          1         400   
2160    Wed Apr 04 18:42:55 +0000 2012       1          1         317   
2962    Fri Apr 06 14:29:43 +0000 2012       1          1         742   
3457    Sat Apr 07 16:00:15 +0000 2012       1          1         979   
3529    Sat Apr 07 16:40:40 +0000 2012       1          1         120   
...                                ...     ...        ...         ...   
225605  Mon Feb 11 23:30:11 +0000 2013       1          1         453   
225890  Tue Feb 12 12:50:07 +0000 2013       1          1         550   
226357  Wed Feb 13 00:43:11 +0000 2013       1          1         311   
227145  Thu Feb 14 00:56:44 +0000 2013       1          1         399   
227282  Thu Feb 14 05:35:43 +0000 2013       1          1        1019   

        InfectionTime        Time  InfectionLongitude  InfectionLatitude  
2013       1333560303  1333560303          -73.987924          40.742188  
2160       1333564975  1333564975          -73.941860          40.833165  
2962       1333722583  1333722583          -73.990568          40.735734  
3457       1333814415  1333814415          -73.990560          40.736527  
3529       1333816840  1333816840          -73.988880          40.602590  
...               ...         ...                 ...                ...  
225605     1360625411  1360625411          -73.991547          40.757221  
225890     1360673407  1360673407          -73.993576          40.750795  
226357     1360716191  1360716191          -73.741902          40.725541  
227145     1360803404  1360803404          -73.984705          40.769619  
227282     1360820143  1360820143  

## Visualize Spatially
Convert to Spatially Enabled DataFrame

Source: https://developers.arcgis.com/python/guide/install-and-set-up/
The map widget is only supported within Jupyter applications. Follow these additional steps to use the map widget in a disconnected environment:

    install the jupyterlab package for visualizing with maps in either Jupyter Notebook or Jupyter Lab:

    conda install jupyterlab

    enable the map widget by running these 2 commands in succession:

        jupyter nbextension enable --py --sys-prefix widgetsnbextension

        jupyter nbextension enable --py --sys-prefix arcgis


In [20]:
sdf = pd.DataFrame.spatial.from_xy(infected_df, 'Longitude','Latitude')
type(sdf)

/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_io/fileops.py:150: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['SHAPE'] = geoms
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_accessor.py:1021: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[r

pandas.core.frame.DataFrame

In [22]:
pdx_map_nyc = gis.map('New York City, NY')
pdx_map_nyc.basemap = 'topo'
pdx_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [23]:
infected_df.spatial.plot(map_widget=pdx_map)

/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/pandas/core/generic.py:6245: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_accessor.py:2317: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._data['OBJECTID'] = list(range(1, self._data.shape[0] + 1))
/opt/anaconda3/envs/cs293b/lib/python3.7/site-packages/arcgis/features/geo/_accessor.py:2362: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. I

True

In [29]:
pdx_map_tko = gis.map('Tokyo')
pdx_map_tko.basemap = 'topo'
pdx_map_tko

MapView(layout=Layout(height='400px', width='100%'))

In [30]:
infected_df.spatial.plot(map_widget=pdx_map_tko)

True

## Explore density of infections

In [31]:
pdx_density_map_nyc = gis.map('New York City, NY')
pdx_density_map_nyc.basemap='gray'
pdx_density_map_nyc

MapView(layout=Layout(height='400px', width='100%'))

In [33]:
infected_df.spatial.plot(map_widget=pdx_density_map_nyc, renderer_type='h')

True